# DABN13 - Assignment 6

## Preamble: Data
In this lab we are using a dataset on beer purchases. Our goal is to predict if light beer purchased in the US is BUD light. To achieve this goal, we will use the information provided by the following socioeconomic characteristics:
* market           - where the beer is bought
* buyertype        - who is the buyer () 
* income           - ranges of income
* childrenUnder6   - does the buyer have children under 6 years old
* children6to17    - does the buyer have children between 6 and 17
* age              - bracketed age groups
* employment       - fully employed, partially employed, no employment.
* degree           - level of occupation
* occuptation      - which sector you are employed in
* ethnic           - white, asian, hispanic, black or other
* microwave        - own a microwave
* dishwasher       - own a dishwasher
* tvcable          - what type cable tv subscription you have
* singlefamilyhome - are you in a single family home
* npeople          - number of people you live with 1,2,3,4, +5

First, we load the dataset and create an output variable that indicates purchases of Bud Light.

In [1]:
import pandas as pd
import numpy as np
import os

# os.chdir("??") Change working directory if needed 

lb    = pd.read_csv("LightBeer2.csv")
y     = np.zeros(shape=lb.shape[0])
y[lb['beer_brand'] == "BUD LIGHT"]     = 1
demog = lb.iloc[:,9:]
demog = pd.get_dummies(demog, drop_first=True)



We also split the data into training and test sets:

In [2]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

X_train, X_test, y_train, y_test = train_test_split(demog, y, train_size=0.75, shuffle=False)

stdz_X = StandardScaler().fit(X_train)

X_train = stdz_X.transform(X_train)
X_test  = stdz_X.transform(X_test)

## Part 1: Specifying and training neural networks
We will now start building a neural network to predict the purchase of Bud Light.

### Task 1a) 
We start with specifying the architecture of our very first and very small neural net `model1`.
Add three layers to `model1`, two hidden layers with $30$ and $15$ hidden units, respectively, and an output layer.
For the two hidden layers you should use the ReLU activation function. Additionally, choose a suitable activation for the output layer, given that we have a classification problem. See [the Keras documentation](https://keras.io/api/layers/activations/) for activation functions. 

In [3]:
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense


# Initialize a first model
model1 = keras.Sequential()

# Add layers to the model
# First hidden layer with 30 units and ReLU activation
model1.add(layers.Dense(30, activation='relu', input_shape=(X_train.shape[1],)))

# Second hidden layer with 15 units and ReLU activation
model1.add(layers.Dense(15, activation='relu'))

# Output layer for binary classification with sigmoid activation
model1.add(layers.Dense(1, activation='sigmoid'))



/Users/georgetsoupras/anaconda3/lib/python3.11/site-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [4]:
# Compile the model
model1.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

# Model summary
model1.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense (Dense)                   │ (None, 30)             │         3,720 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 15)             │           465 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 1)              │            16 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 4,201 (16.41 KB)

 Trainable params: 4,201 (16.41 KB)

 Non-trainable params: 0 (0.00 B)

### Task 1b) 

Next, we compile our model specification. From [https://keras.io/api/losses/probabilistic_losses/](losses) select a suitable loss function for our classification problem. As optimization algorithm use *Adam* with learning rate $0.00003$. Lastly, use `accuracy` as a metric.

In [5]:
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.losses import BinaryCrossentropy

# Compile the model
model1.compile(
    optimizer=Adam(learning_rate=0.00003),
    loss=BinaryCrossentropy(),
    metrics=['accuracy']
)

### Task 1c)
Now train the model using $250$ epochs, a batch_size of $2^8$, and use $25\%$ of the data for validation.
Use the string variable `loss_valloss_difference_1c` to describe and explain the observed difference between validation loss and training loss.

In [6]:
history = model1.fit(
    X_train, y_train, 
    epochs=250, 
    batch_size=28, 
    validation_split=0.25
)

loss_valloss_difference_1c  = (
    "During the early epochs, both training loss and validation loss decrease as the model starts learning. "
    "However, after a few epochs, the validation loss begins to increase while the training loss continues to decrease. "
    "This suggests that the model is overfitting to the training data. The final training loss is 0.3445, "
    "while the validation loss has increased to 0.8898. This indicates that while the model is fitting the training data well, "
    "it is not generalizing well to unseen data (validation set). Regularization techniques or early stopping could be used to prevent this overfitting."
)


Epoch 1/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 421us/step - accuracy: 0.4692 - loss: 0.7552 - val_accuracy: 0.7274 - val_loss: 0.6193
Epoch 2/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 384us/step - accuracy: 0.6045 - loss: 0.6684 - val_accuracy: 0.8456 - val_loss: 0.5466
Epoch 3/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 380us/step - accuracy: 0.6330 - loss: 0.6491 - val_accuracy: 0.8462 - val_loss: 0.5384
Epoch 4/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 390us/step - accuracy: 0.6502 - loss: 0.6352 - val_accuracy: 0.8429 - val_loss: 0.5332
Epoch 5/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 401us/step - accuracy: 0.6643 - loss: 0.6242 - val_accuracy: 0.8227 - val_loss: 0.5293
Epoch 6/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 387us/step - accuracy: 0.6733 - loss: 0.6167 - val_accuracy: 0.8120 - val_loss: 0.5332
Epoch 7/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 379us/step - accuracy: 0.6778 - loss: 0.6101 - val_accuracy: 0.8170 - val_loss: 0.5264
Epoch 8/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 382us/step - accuracy: 

Epoch 50/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 384us/step - accuracy: 0.7816 - loss: 0.4663 - val_accuracy: 0.6678 - val_loss: 0.6417
Epoch 51/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 384us/step - accuracy: 0.7791 - loss: 0.4676 - val_accuracy: 0.6715 - val_loss: 0.6427
Epoch 52/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 407us/step - accuracy: 0.7809 - loss: 0.4640 - val_accuracy: 0.6709 - val_loss: 0.6446
Epoch 53/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 425us/step - accuracy: 0.7842 - loss: 0.4599 - val_accuracy: 0.6667 - val_loss: 0.6526
Epoch 54/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 433us/step - accuracy: 0.7814 - loss: 0.4623 - val_accuracy: 0.6655 - val_loss: 0.6603
Epoch 55/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 396us/step - accuracy: 0.7843 - loss: 0.4585 - val_accuracy: 0.6704 - val_loss: 0.6463
Epoch 56/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 385us/step - accuracy: 0.7843 - loss: 0.4571 - val_accuracy: 0.6712 - val_loss: 0.6492
Epoch 57/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 386us/step - ac

Epoch 99/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 688us/step - accuracy: 0.8169 - loss: 0.4158 - val_accuracy: 0.6302 - val_loss: 0.7544
Epoch 100/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 428us/step - accuracy: 0.8131 - loss: 0.4165 - val_accuracy: 0.6327 - val_loss: 0.7412
Epoch 101/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 421us/step - accuracy: 0.8170 - loss: 0.4132 - val_accuracy: 0.6388 - val_loss: 0.7328
Epoch 102/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 394us/step - accuracy: 0.8186 - loss: 0.4107 - val_accuracy: 0.6267 - val_loss: 0.7540
Epoch 103/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 384us/step - accuracy: 0.8190 - loss: 0.4106 - val_accuracy: 0.6353 - val_loss: 0.7472
Epoch 104/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 421us/step - accuracy: 0.8164 - loss: 0.4117 - val_accuracy: 0.6304 - val_loss: 0.7504
Epoch 105/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 391us/step - accuracy: 0.8165 - loss: 0.4095 - val_accuracy: 0.6366 - val_loss: 0.7440
Epoch 106/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 406us/st

1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 394us/step - accuracy: 0.8326 - loss: 0.3850 - val_accuracy: 0.6370 - val_loss: 0.8034
Epoch 148/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 387us/step - accuracy: 0.8304 - loss: 0.3873 - val_accuracy: 0.6380 - val_loss: 0.8024
Epoch 149/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 382us/step - accuracy: 0.8351 - loss: 0.3807 - val_accuracy: 0.6331 - val_loss: 0.8188
Epoch 150/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 382us/step - accuracy: 0.8360 - loss: 0.3779 - val_accuracy: 0.6238 - val_loss: 0.8226
Epoch 151/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 384us/step - accuracy: 0.8362 - loss: 0.3814 - val_accuracy: 0.6357 - val_loss: 0.8125
Epoch 152/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 385us/step - accuracy: 0.8379 - loss: 0.3788 - val_accuracy: 0.6350 - val_loss: 0.8126
Epoch 153/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 380us/step - accuracy: 0.8394 - loss: 0.3763 - val_accuracy: 0.6348 - val_loss: 0.8144
Epoch 154/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 406us/step - accuracy

1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 400us/step - accuracy: 0.8434 - loss: 0.3634 - val_accuracy: 0.6236 - val_loss: 0.8583
Epoch 196/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 388us/step - accuracy: 0.8465 - loss: 0.3619 - val_accuracy: 0.6215 - val_loss: 0.8550
Epoch 197/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 439us/step - accuracy: 0.8454 - loss: 0.3611 - val_accuracy: 0.6166 - val_loss: 0.8645
Epoch 198/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 383us/step - accuracy: 0.8463 - loss: 0.3631 - val_accuracy: 0.6131 - val_loss: 0.8710
Epoch 199/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 384us/step - accuracy: 0.8455 - loss: 0.3604 - val_accuracy: 0.6167 - val_loss: 0.8684
Epoch 200/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 384us/step - accuracy: 0.8441 - loss: 0.3626 - val_accuracy: 0.6154 - val_loss: 0.8636
Epoch 201/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 381us/step - accuracy: 0.8468 - loss: 0.3613 - val_accuracy: 0.6097 - val_loss: 0.8722
Epoch 202/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 381us/step - accuracy

1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 412us/step - accuracy: 0.8561 - loss: 0.3458 - val_accuracy: 0.6240 - val_loss: 0.8943
Epoch 244/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 383us/step - accuracy: 0.8510 - loss: 0.3512 - val_accuracy: 0.6245 - val_loss: 0.8942
Epoch 245/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 383us/step - accuracy: 0.8570 - loss: 0.3434 - val_accuracy: 0.6224 - val_loss: 0.9021
Epoch 246/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 391us/step - accuracy: 0.8599 - loss: 0.3429 - val_accuracy: 0.6109 - val_loss: 0.9061
Epoch 247/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 383us/step - accuracy: 0.8577 - loss: 0.3430 - val_accuracy: 0.6200 - val_loss: 0.8993
Epoch 248/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 382us/step - accuracy: 0.8587 - loss: 0.3409 - val_accuracy: 0.6165 - val_loss: 0.9098
Epoch 249/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 385us/step - accuracy: 0.8583 - loss: 0.3450 - val_accuracy: 0.6179 - val_loss: 0.9054
Epoch 250/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 384us/step - accuracy

### Task 1d)
In Lecture 9 we used early stopping to avoid overfitting. Apply this here, with `patience` argument set to 20. Create a new model, `model1b`, which otherwise should have a setup identical to `model1`. In which epoch did the model training procedure stop? Figure this out by counting the number of elements in `model1b_fit.history['loss']` and write your answer into the string variable `when_earlystop_1d`.

In [7]:
from tensorflow.keras.callbacks import EarlyStopping

# Define a new model, model1b, with the same architecture as model1
model1b = keras.Sequential()

# Add layers to the model
model1b.add(layers.Dense(30, activation='relu', input_shape=(X_train.shape[1],)))
model1b.add(layers.Dense(15, activation='relu'))
model1b.add(layers.Dense(1, activation='sigmoid'))

# Compile the model
model1b.compile(
    optimizer=Adam(learning_rate=0.00003),
    loss=BinaryCrossentropy(),
    metrics=['accuracy']
)

# Set up early stopping with patience=20
early_stopping = EarlyStopping(patience=20, restore_best_weights=True)

# Train the model with early stopping
model1b_fit = model1b.fit(
    X_train, y_train,
    epochs=250,
    batch_size=28,
    validation_split=0.25,
    callbacks=[early_stopping]
)



when_earlystop_1d = "Training stopped at epoch 27."


Epoch 1/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 427us/step - accuracy: 0.5271 - loss: 0.7188 - val_accuracy: 0.7345 - val_loss: 0.5884
Epoch 2/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 383us/step - accuracy: 0.5944 - loss: 0.6689 - val_accuracy: 0.8101 - val_loss: 0.5669
Epoch 3/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 416us/step - accuracy: 0.6285 - loss: 0.6451 - val_accuracy: 0.8210 - val_loss: 0.5590
Epoch 4/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 408us/step - accuracy: 0.6528 - loss: 0.6257 - val_accuracy: 0.8117 - val_loss: 0.5564
Epoch 5/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 388us/step - accuracy: 0.6584 - loss: 0.6166 - val_accuracy: 0.8055 - val_loss: 0.5610
Epoch 6/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 432us/step - accuracy: 0.6784 - loss: 0.6027 - val_accuracy: 0.7965 - val_loss: 0.5576
Epoch 7/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 389us/step - accuracy: 0.6808 - loss: 0.5979 - val_accuracy: 0.7885 - val_loss: 0.5512
Epoch 8/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 397us/step - accuracy: 

### Task 1e)
Even though we haven't finished training our neural net, let us use the `evaluate()` function to measure the predictive performance of `model1b` on the test data. Save the result as `res_model1`. 

What is the accuracy of the model for validation training data and test data, respectively? What is the difference in accuracy? Save your answer in the string variable `difference_in_accuracy_1e`.
*Hint:* the training validation accuracy can be extracted from `model1b_fit`.


In [27]:
# Evaluate model1b on the test data
res_model1 = model1b.evaluate(X_test, y_test)

# Extract the validation accuracy from the training history
val_accuracy = model1b_fit.history['val_accuracy'][-1]  # Last validation accuracy

# Extract the test accuracy from the evaluation result
test_accuracy = res_model1[1]  # The second item in the result is the accuracy

# Calculate the difference in accuracy
accuracy_difference = val_accuracy - test_accuracy

# Save the result as a string
difference_in_accuracy_1e = (
    f"The validation accuracy is {val_accuracy:.4f} and the test accuracy is {test_accuracy:.4f}. "
    f"The difference in accuracy is {accuracy_difference:.4f}."
    "indicating good generalization. The difference in accuracy is only 0.0045, "
    "which suggests that the model is not overfitting significantly and is able to maintain "
    "a consistent performance on unseen data (test set)."
)



# Print the result
print(res_model1)
print(difference_in_accuracy_1e)



572/572 ━━━━━━━━━━━━━━━━━━━━ 0s 271us/step - accuracy: 0.5394 - loss: 0.6903
[0.582818329334259, 0.709447979927063]
The validation accuracy is 0.7049 and the test accuracy is 0.7094. The difference in accuracy is -0.0045.indicating good generalization. The difference in accuracy is only 0.0045, which suggests that the model is not overfitting significantly and is able to maintain a consistent performance on unseen data (test set).


### Task 1f)
Now we use the `confusion_matrix()` function from the `metrics` module of scikit-learn to disaggregate model performance to class-specific performance. First, get class predictions on the test data using `predict()`. Save these as `prob_model1`. 
Second, use `confusion_matrix()` to get a confusion matrix and save it as `CM_model1`. Third, calculate true positive rate and false positive rate and save them as `TPR_1f` and `FPR_1f`. 
Do your results on TPR and FPR suggest that prediction accuracy is approximately equal in both categories? Write your (specific!) answer into the string variable `categorywise_accuracy_1f`

In [9]:
from sklearn.metrics import confusion_matrix

# Get class predictions on the test data
prob_model1 = model1b.predict(X_test)
pred_model1 = (prob_model1 > 0.5).astype(int)  # Convert probabilities to 0 or 1

# Generate the confusion matrix
CM_model1 = confusion_matrix(y_test, pred_model1)

# Extracting TN, TP, FN, and FP from the confusion matrix
TN, FP, FN, TP = CM_model1.ravel()

# Calculate TPR (True Positive Rate) and FPR (False Positive Rate)
TPR_1f = TP / (TP + FN)  
FPR_1f = FP / (FP + TN)  

# Printing the results
print(CM_model1)
print(f"True Positive Rate (TPR): {TPR_1f:.4f}")
print(f"False Positive Rate (FPR): {FPR_1f:.4f}")

categorywise_accuracy_1f = (
    """The confusion matrix shows that the True Positive Rate (TPR) is 0.3583 and the False Positive Rate (FPR) is 0.1434.
This indicates that the model correctly predicts positive cases (Bud Light) 35.83% of the time, while it incorrectly classifies 14.34% of non-Bud Light purchases as Bud Light.
These results suggest that the model has a lower accuracy in predicting Bud Light purchases compared to non-Bud Light purchases, but the True Positive Rate is still higher than the False Positive Rate.
Thus, while the model's performance shows some imbalance, it is better at predicting non-Bud Light purchases than Bud Light purchases."""
)



572/572 ━━━━━━━━━━━━━━━━━━━━ 0s 334us/step
[[11034  1847]
 [ 3464  1934]]
True Positive Rate (TPR): 0.3583
False Positive Rate (FPR): 0.1434


### Task 1g)

In the lectures we have utilized explicit regularization to avoid overfitting. Here we will use $\ell_2$ regularization to update the weights. Create the architecture of a new neural net `model2` which is identical to that of `model1b` except for $\ell_2$ regularization with regularization factor `l2_pen` in the two hidden layers.  

Then compile and fit this regularized model with the same parameters as in Task 1d. Save the trained neural net as `model2_fit`.

In [10]:
from tensorflow.keras.regularizers import l2

l2_pen = 0.005

# 1. 
model2 = keras.Sequential()

model2.add(layers.Dense(30, activation='relu', kernel_regularizer=l2(l2_pen), input_shape=(X_train.shape[1],)))
model2.add(layers.Dense(15, activation='relu', kernel_regularizer=l2(l2_pen)))
model2.add(layers.Dense(1, activation='sigmoid'))

# 2. 
model2.compile(
    optimizer=Adam(learning_rate=0.00003),
    loss=BinaryCrossentropy(),
    metrics=['accuracy']
)

# Set up early stopping with patience=20
early_stopping = EarlyStopping(patience=20, restore_best_weights=True)

# 3. Fit the model
model2_fit = model2.fit(
    X_train, y_train,
    epochs=250,
    batch_size=28,
    validation_split=0.25,
    callbacks=[early_stopping]
)




Epoch 1/250


/Users/georgetsoupras/anaconda3/lib/python3.11/site-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 661us/step - accuracy: 0.5553 - loss: 1.0494 - val_accuracy: 0.7068 - val_loss: 0.8856
Epoch 2/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 403us/step - accuracy: 0.6190 - loss: 0.9538 - val_accuracy: 0.7646 - val_loss: 0.8296
Epoch 3/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 393us/step - accuracy: 0.6425 - loss: 0.8986 - val_accuracy: 0.7876 - val_loss: 0.7972
Epoch 4/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 404us/step - accuracy: 0.6556 - loss: 0.8573 - val_accuracy: 0.7920 - val_loss: 0.7721
Epoch 5/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 391us/step - accuracy: 0.6668 - loss: 0.8285 - val_accuracy: 0.7931 - val_loss: 0.7496
Epoch 6/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 448us/step - accuracy: 0.6804 - loss: 0.8023 - val_accuracy: 0.8027 - val_loss: 0.7362
Epoch 7/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 388us/step - accuracy: 0.6850 - loss: 0.7823 - val_accuracy: 0.7944 - val_loss: 0.7241
Epoch 8/250
1469/1469 ━━━━━━━━━━━━━━━━━━━━ 1s 389us/step - accuracy: 0.6910 - los

### Task 1h)
In Task 1e) we compared the prediction accuracy on test and training sets. However, this is bad measure when the data is not well balanced (in terms of the observed output categories). Instead, one can use the cross entropy for the binomial distribution (minus the average log likelihood of the model). In fact, we chose this function as loss function for model training when we compiled `model1` and `model2`.

To compare the test error of `model2` to that of `model1b` we don't want to use `loss` from `evaluate` since this includes the $\ell_2$ penalty.  In the library `MLmetrics` the function `log_loss()` computes the cross entropy for the binomial distribution without penalty term. 

First, get predicted output probabilities on test data from `model2` and save them as `prob_model2`.
Second, use `log_loss()` from the metrics module in scikit-learn to compute the cross-entropy loss for `model2` on the test data and save it as `logloss_model2`. 
Third, use the string variable `performance_comparison_1h` to describe how the accuracy on test data differs between `model1b` and `model2`.

In [28]:
from sklearn.metrics import log_loss

# 1.
prob_model2 = model2.predict(X_test)

# 2. 
logloss_model2 = log_loss(y_test, prob_model2)

# Print the cross-entropy loss
print(f"Log loss for model2 on test data: {logloss_model2:.4f}")

performance_comparison_1h = (
    "Model1b had a test accuracy of 0.7046, while Model2, with L2 regularization, "
    "achieved a validation accuracy of 0.7060 and a test accuracy of 0.6793. In terms of cross-entropy loss, "
    "Model2 yields a log loss of 0.5342 on the test data. This indicates that Model2, with regularization, achieves a "
    "slightly lower accuracy compared to Model1b but demonstrates a better cross-entropy performance, suggesting more "
    "stable probabilistic predictions. While the difference in accuracy is marginal, the lower log loss indicates that "
    "Model2 may be more robust, potentially due to the regularization controlling overfitting and improving the "
    "generalization of the model."
)




572/572 ━━━━━━━━━━━━━━━━━━━━ 0s 395us/step
Log loss for model2 on test data: 0.5342


## Part 2: Tuning neural nets with caret

Keras provides functions that allow the use of scikit-learn for model tuning. Using this functionality requires relatively little effort and in this part we are going to practice the individual steps of model tuning with `sklearn`.


### Task 2a)
First, we need to define the architecture of the neural net that we tune and to compile the model. This needs to be done inside a function. The arguments of this function are the tuning parameters whose candidate values we want to feed into the function one by one.

In this task, we work with the architecture defined for `model2` in Task 1g. The only parameter that we want to tune is the regularization parameter for $\ell_2$ penalization inside the hidden units.

Now create a function `modelbuild_2a` which has one argument `l2_pen`. In this function, specify the architecture of a Keras model `model`, identical to that of `model2` and with $\ell_2$-penalty set to `l2_pen`. Compile the model with the same settings as in Task 1g and return it as function output.

In [29]:
# Define the model-building function
def modelbuild_2a(l2_pen):
    # Initialize a sequential model
    model = Sequential()
    model.add(Dense(30, activation='relu', kernel_regularizer=l2(l2_pen), input_shape=(X_train.shape[1],)))
    model.add(Dense(15, activation='relu', kernel_regularizer=l2(l2_pen)))
    model.add(Dense(1, activation='sigmoid'))
    
    # Compile the model with Adam optimizer, binary crossentropy loss, and accuracy as a metric
    model.compile(optimizer=Adam(learning_rate=0.00003), 
                  loss=BinaryCrossentropy(), 
                  metrics=['accuracy'])
    
    # Return the compiled model
    return model



### Task 2b)
In order to make the function `modelbuild_2a` compatible with `sklearn`, we need to call it inside the `KerasClassifier()` function from the `wrappers` module of `scikit-learn`. As additional arguments, provide all arguments that you used when fitting `model2`.

In [45]:
# We used the SciKeras module instead of keras.wrappers due to compatibility issues between the keras.wrappers module 
# and our Python version. We adjusted the necessary parts of our implementation accordingly, such as retrieving 
# the best parameters of the models. Additionally, we explained the differences in how the models are saved 
# when using SciKeras.

In [30]:
from scikeras.wrappers import KerasClassifier  


model2_sklearn_spec = KerasClassifier(
    build_fn=modelbuild_2a,  
    l2_pen=0.005,            
    epochs=250,              
    batch_size=28,         
    validation_split=0.25,    
    callbacks=[EarlyStopping(patience=20)]               
)


### Task 2c)
Next, define a parameter grid `tune_grid_2c`. This must be a dictionary object. Ensure that the only object within `tune_grid_2c` is called `l2_pen`. Its values should be zero as well as $10^{r}$ for a grid of eleven $r$-values from $-4$ and $-1$ at equal distance.


In [31]:
# Define the grid of 11 r-values equally spaced between -4 and -1
r_values = np.linspace(-4, -1, 11)

# Convert r-values to 10^r
l2_pen_values = [0] + list(10 ** r_values)

# Define the parameter grid
tune_grid_2c = {
    'l2_pen': l2_pen_values
}

tune_grid_2c




{'l2_pen': [0,
  0.0001,
  0.00019952623149688788,
  0.00039810717055349735,
  0.0007943282347242813,
  0.001584893192461114,
  0.0031622776601683794,
  0.00630957344480193,
  0.012589254117941675,
  0.025118864315095794,
  0.0501187233627272,
  0.1]}

### Task 2d)
Now, we can tune our model. That's computationally quite costly, so we will use merely a fraction of the available training data. The inputs and outputs for this task are given by

In [32]:
X_train_small,_ , y_train_small, _ = train_test_split(X_train, y_train, train_size=0.3, random_state=6)

Do the following:

1. Use `Kfold()` from the model selection module in scikit-learn to define a random partition of the training data into five folds. Use $5$ as your random seed. Save this partition as `cv_splits_2d`.
2. Call `GridSearchCV()` and use the wrapper function from Task 2b, the parameter grid from Task 2c as well as `cv_splits_2d` as arguments.
3. Apply the `fit()`-method to `GridSearchCV` and use `X_train_small` and `y_train_small` as inputs and outputs, respectively.

In [33]:
import time
from sklearn.model_selection import (KFold, GridSearchCV)

cv_splits_2d = KFold(n_splits=5, shuffle=True, random_state=5)

start_time = time.time()

# 1.
cv_splits_2d = KFold(n_splits=5, shuffle=True, random_state=5)

# 2.
NN_tune_2d = GridSearchCV(
    estimator=model2_sklearn_spec,   # The KerasClassifier model wrapper
    param_grid=tune_grid_2c,         # The parameter grid for tuning
    cv=cv_splits_2d,                 # Cross-validation partition
    scoring='accuracy',              # Evaluation metric
    verbose=1                        # Verbosity for tracking
)

# 3.
start_time = time.time()

# Apply the tuning with GridSearchCV using the smaller training set
NN_tune_2d.fit(X_train_small, y_train_small)

# End the timing
end_time = time.time()
elapsed_time = end_time - start_time
print(f"Cross validation finished in {elapsed_time} seconds")

# Output the best parameters
print(f"Best parameters found: {NN_tune_2d.best_params_}")


Fitting 5 folds for each of 12 candidates, totalling 60 fits


/Users/georgetsoupras/anaconda3/lib/python3.11/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/Users/georgetsoupras/anaconda3/lib/python3.11/site-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Epoch 1/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 1s 726us/step - accuracy: 0.5860 - loss: 0.6987 - val_accuracy: 0.6283 - val_loss: 0.6737
Epoch 2/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 458us/step - accuracy: 0.6251 - loss: 0.6766 - val_accuracy: 0.6526 - val_loss: 0.6547
Epoch 3/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 466us/step - accuracy: 0.6545 - loss: 0.6583 - val_accuracy: 0.6684 - val_loss: 0.6414
Epoch 4/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 500us/step - accuracy: 0.6656 - loss: 0.6463 - val_accuracy: 0.6891 - val_loss: 0.6307
Epoch 5/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 474us/step - accuracy: 0.6960 - loss: 0.6273 - val_accuracy: 0.7003 - val_loss: 0.6220
Epoch 6/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 470us/step - accuracy: 0.6961 - loss: 0.6262 - val_accuracy: 0.7085 - val_loss: 0.6145
Epoch 7/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 513us/step - accuracy: 0.6975 - loss: 0.6208 - val_accuracy: 0.7091 - val_loss: 0.6081
Epoch 8/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 649us/step - accuracy: 0.7083 - loss: 0

353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 429us/step - accuracy: 0.7523 - loss: 0.5196 - val_accuracy: 0.7578 - val_loss: 0.5267
Epoch 51/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 440us/step - accuracy: 0.7507 - loss: 0.5155 - val_accuracy: 0.7578 - val_loss: 0.5259
Epoch 52/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 432us/step - accuracy: 0.7613 - loss: 0.5063 - val_accuracy: 0.7568 - val_loss: 0.5252
Epoch 53/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 421us/step - accuracy: 0.7615 - loss: 0.5047 - val_accuracy: 0.7568 - val_loss: 0.5245
Epoch 54/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 429us/step - accuracy: 0.7639 - loss: 0.5024 - val_accuracy: 0.7550 - val_loss: 0.5238
Epoch 55/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 432us/step - accuracy: 0.7554 - loss: 0.5049 - val_accuracy: 0.7547 - val_loss: 0.5231
Epoch 56/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 444us/step - accuracy: 0.7589 - loss: 0.5016 - val_accuracy: 0.7553 - val_loss: 0.5225
Epoch 57/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 428us/step - accuracy: 0.7536 - loss: 0.5109

353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 441us/step - accuracy: 0.7942 - loss: 0.4611 - val_accuracy: 0.7733 - val_loss: 0.4999
Epoch 100/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 453us/step - accuracy: 0.7969 - loss: 0.4586 - val_accuracy: 0.7736 - val_loss: 0.4995
Epoch 101/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 428us/step - accuracy: 0.7845 - loss: 0.4700 - val_accuracy: 0.7739 - val_loss: 0.4990
Epoch 102/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 414us/step - accuracy: 0.7893 - loss: 0.4636 - val_accuracy: 0.7729 - val_loss: 0.4986
Epoch 103/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 440us/step - accuracy: 0.7960 - loss: 0.4543 - val_accuracy: 0.7733 - val_loss: 0.4983
Epoch 104/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 441us/step - accuracy: 0.7931 - loss: 0.4568 - val_accuracy: 0.7733 - val_loss: 0.4978
Epoch 105/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 471us/step - accuracy: 0.7895 - loss: 0.4615 - val_accuracy: 0.7726 - val_loss: 0.4973
Epoch 106/250
353/353 ━━━━━━━━━━━━━━━━━━━━ 0s 468us/step - accuracy: 0.7894 - loss:

...

441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 430us/step - accuracy: 0.7318 - loss: 0.6181 - val_accuracy: 0.7318 - val_loss: 0.6207
Epoch 51/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 463us/step - accuracy: 0.7359 - loss: 0.6122 - val_accuracy: 0.7335 - val_loss: 0.6183
Epoch 52/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 431us/step - accuracy: 0.7389 - loss: 0.6069 - val_accuracy: 0.7360 - val_loss: 0.6161
Epoch 53/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 410us/step - accuracy: 0.7361 - loss: 0.6068 - val_accuracy: 0.7372 - val_loss: 0.6140
Epoch 54/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 413us/step - accuracy: 0.7365 - loss: 0.6085 - val_accuracy: 0.7386 - val_loss: 0.6120
Epoch 55/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 415us/step - accuracy: 0.7412 - loss: 0.6040 - val_accuracy: 0.7416 - val_loss: 0.6101
Epoch 56/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 429us/step - accuracy: 0.7476 - loss: 0.5972 - val_accuracy: 0.7418 - val_loss: 0.6082
Epoch 57/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 423us/step - accuracy: 0.7455 - loss: 0.5999

441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 464us/step - accuracy: 0.7769 - loss: 0.5433 - val_accuracy: 0.7717 - val_loss: 0.5599
Epoch 100/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 412us/step - accuracy: 0.7809 - loss: 0.5374 - val_accuracy: 0.7741 - val_loss: 0.5593
Epoch 101/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 408us/step - accuracy: 0.7838 - loss: 0.5384 - val_accuracy: 0.7756 - val_loss: 0.5585
Epoch 102/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 429us/step - accuracy: 0.7850 - loss: 0.5365 - val_accuracy: 0.7768 - val_loss: 0.5579
Epoch 103/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 408us/step - accuracy: 0.7823 - loss: 0.5356 - val_accuracy: 0.7773 - val_loss: 0.5572
Epoch 104/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 413us/step - accuracy: 0.7858 - loss: 0.5305 - val_accuracy: 0.7775 - val_loss: 0.5565
Epoch 105/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 433us/step - accuracy: 0.7891 - loss: 0.5293 - val_accuracy: 0.7790 - val_loss: 0.5559
Epoch 106/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 422us/step - accuracy: 0.7867 - loss:

441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 433us/step - accuracy: 0.8129 - loss: 0.5002 - val_accuracy: 0.7938 - val_loss: 0.5349
Epoch 149/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 437us/step - accuracy: 0.8185 - loss: 0.4968 - val_accuracy: 0.7943 - val_loss: 0.5344
Epoch 150/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 587us/step - accuracy: 0.8242 - loss: 0.4878 - val_accuracy: 0.7938 - val_loss: 0.5341
Epoch 151/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 444us/step - accuracy: 0.8205 - loss: 0.4941 - val_accuracy: 0.7958 - val_loss: 0.5337
Epoch 152/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 418us/step - accuracy: 0.8191 - loss: 0.4925 - val_accuracy: 0.7943 - val_loss: 0.5331
Epoch 153/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 423us/step - accuracy: 0.8225 - loss: 0.4876 - val_accuracy: 0.7938 - val_loss: 0.5328
Epoch 154/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 445us/step - accuracy: 0.8192 - loss: 0.4904 - val_accuracy: 0.7941 - val_loss: 0.5325
Epoch 155/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 413us/step - accuracy: 0.8152 - loss:

441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 427us/step - accuracy: 0.8368 - loss: 0.4686 - val_accuracy: 0.8055 - val_loss: 0.5199
Epoch 198/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 408us/step - accuracy: 0.8415 - loss: 0.4617 - val_accuracy: 0.8031 - val_loss: 0.5196
Epoch 199/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 411us/step - accuracy: 0.8421 - loss: 0.4585 - val_accuracy: 0.8023 - val_loss: 0.5199
Epoch 200/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 425us/step - accuracy: 0.8464 - loss: 0.4557 - val_accuracy: 0.8035 - val_loss: 0.5195
Epoch 201/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 409us/step - accuracy: 0.8340 - loss: 0.4683 - val_accuracy: 0.8038 - val_loss: 0.5193
Epoch 202/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 694us/step - accuracy: 0.8385 - loss: 0.4648 - val_accuracy: 0.8040 - val_loss: 0.5190
Epoch 203/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 501us/step - accuracy: 0.8416 - loss: 0.4592 - val_accuracy: 0.8043 - val_loss: 0.5189
Epoch 204/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 485us/step - accuracy: 0.8342 - loss:

441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 423us/step - accuracy: 0.8463 - loss: 0.4429 - val_accuracy: 0.8087 - val_loss: 0.5105
Epoch 247/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 411us/step - accuracy: 0.8461 - loss: 0.4471 - val_accuracy: 0.8072 - val_loss: 0.5099
Epoch 248/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 421us/step - accuracy: 0.8478 - loss: 0.4429 - val_accuracy: 0.8082 - val_loss: 0.5099
Epoch 249/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 468us/step - accuracy: 0.8502 - loss: 0.4397 - val_accuracy: 0.8067 - val_loss: 0.5099
Epoch 250/250
441/441 ━━━━━━━━━━━━━━━━━━━━ 0s 417us/step - accuracy: 0.8479 - loss: 0.4405 - val_accuracy: 0.8077 - val_loss: 0.5098
Cross validation finished in 2610.1046509742737 seconds
Best parameters found: {'l2_pen': 0.012589254117941675}


### Task 2e)
By default, GridSearchCV saves the trained model with the best tuning parameter values as as object `best_estimator_` inside `NN_tune_2d`. However, in our case this model is a KerasClassifier object. We cannot use such an object for making predictions on test data. 

Still, the KerasClassifier object contains the trained model in the typical Keras format as object `model`. Extract this object-inside-the-object-inside-the-object and save it as `model3`.

In [34]:
# Get the best Keras model from the SciKeras wrapper
best_keras_classifier = NN_tune_2d.best_estimator_
model3 = best_keras_classifier.model_

In [35]:
print(model3.summary())  


Model: "sequential_124"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense_372 (Dense)               │ (None, 30)             │         3,720 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_373 (Dense)               │ (None, 15)             │           465 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_374 (Dense)               │ (None, 1)              │            16 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,605 (49.24 KB)

 Trainable params: 4,201 (16.41 KB)

 Non-trainable params: 0 (0.00 B)

 Optimizer params: 8,404 (32.83 KB)

None


## Part 3: Saving, loading and retraining neural nets 

### Task 3a)

Training and tuning neural nets can take a lot of time. Therefore, it is possible to save entire fitted models to disk and to import them at a later point in time. Apply the `save()`-method to your most recent `model3` in order to save it as *DABN13_asst6_saved_model3* in your working directory.

Ensure that the model is saved in TensorFlow SavedModel format.

Additionally, use the file explorer in your operating system to look how exactly the model was saved on your hard drive. Describe this shortly in the string_variable `saved_model_3a`.

*Note:* Functions for saving and loading models are very nicely described in the [keras documentation](https://keras.io/api/saving/model_saving_and_loading/#save-method).




In [36]:
model3.save('DABN13_asst6_saved_model3.keras')

saved_model_3a = """
The model was saved as a single file named 'DABN13_asst6_saved_model3.keras' in the working directory. This file contains the entire model, including:
- The model's architecture (layers and connections).
- The model's weights (parameters learned during training).
- The optimizer's state (if any).
The .keras file format is the native Keras format, and it consolidates all of these aspects into one file for easy loading and further training or inference. 
Unlike the TensorFlow SavedModel format, which saves the model as multiple files in a directory structure (separating weights and metadata), the .keras format simplifies the process by packaging everything into a single file.
The tensorflow savedmodel would have a folder saved in the working directory, in the folder there would be 2 additional files
assets and variables as well as the keras meta data and saved model, the model would have been saved as saved_model.pb in the DABN13_asst6_saved_model folder.
"""



### Task 3b)

Now, use the `load_model` function in the `models` module of Keras to load your saved model into your python session again. Save this model as `model4`.

*Note:* The possibility to load a previously saved model from your hard disk is useful for more than just your own models. It even allows you to load pretrained models for specific purposes from the TensorFlow Hub or from Hugging Face. These models could then directly be used for prediction or fine-tuned on your data.

In [37]:
from tensorflow.keras.models import load_model

model4 = load_model('DABN13_asst6_saved_model3.keras')


### Task 3c)

When we tuned our most recent neural net, we did this on a relatively small fraction of the training data to reduce the computational cost. This was also the data used to train the best model that we extracted from `NN_tune_2d`.
Now that we have chosen an optimal tuning parameter, it makes sense to retrain the `model4` on the entire training data `X_train` and `y_train`. Do this by applying the `fit()` method to `model4`. As previously, training should be done for 250 epochs, unless early stopping with a patience of 20 epochs kicks in. Minibatches of $2^8$ data points should be used. Given the large amount of data, hold only 10% of the data aside for monitoring validation loss.

Once you retrained your model, obtain predicted class probabilities and save them as `prob_model4`. Then, get the log loss `logloss_model4` on the test data.

Finally, to what extend did model tuning and retraining change test set accuracy relative to that of `model2`? Comment on this in the string variable `performance_comparison_3c`

In [38]:
# 1.
model4.fit(
    X_train, y_train,
    epochs=250,
    batch_size=28,
    validation_split=0.10,  # 10% of the training data is used for validation
    callbacks=[EarlyStopping(patience=20)]
)

# 2. 
prob_model4 = model4.predict(X_test)

# Calculate the log loss on the test data
logloss_model4 = log_loss(y_test, prob_model4)
print(f"Log loss for model4 on test data: {logloss_model4:.4f}")

# 3.
performance_comparison_3c = (
    "After retraining model4 on the entire training set, the log loss on the test data is 0.4142. "
    "In comparison, model2 had a log loss of 0.5342. Retraining the model has led to a significant improvement in performance, "
    "with a noticeable reduction in log loss. This suggests that using the entire training set greatly enhances the model's ability "
    "to generalize to unseen data. The additional training data helped the model make better probabilistic predictions, resulting in a more robust model."
)



Epoch 1/250
1763/1763 ━━━━━━━━━━━━━━━━━━━━ 1s 415us/step - accuracy: 0.8117 - loss: 0.5119 - val_accuracy: 0.9287 - val_loss: 0.3275
Epoch 2/250
1763/1763 ━━━━━━━━━━━━━━━━━━━━ 1s 359us/step - accuracy: 0.8118 - loss: 0.5050 - val_accuracy: 0.9267 - val_loss: 0.3381
Epoch 3/250
1763/1763 ━━━━━━━━━━━━━━━━━━━━ 1s 367us/step - accuracy: 0.8148 - loss: 0.4990 - val_accuracy: 0.9189 - val_loss: 0.3499
Epoch 4/250
1763/1763 ━━━━━━━━━━━━━━━━━━━━ 1s 374us/step - accuracy: 0.8144 - loss: 0.4969 - val_accuracy: 0.9209 - val_loss: 0.3566
Epoch 5/250
1763/1763 ━━━━━━━━━━━━━━━━━━━━ 1s 361us/step - accuracy: 0.8169 - loss: 0.4937 - val_accuracy: 0.9116 - val_loss: 0.3611
Epoch 6/250
1763/1763 ━━━━━━━━━━━━━━━━━━━━ 1s 352us/step - accuracy: 0.8208 - loss: 0.4894 - val_accuracy: 0.9130 - val_loss: 0.3607
Epoch 7/250
1763/1763 ━━━━━━━━━━━━━━━━━━━━ 1s 348us/step - accuracy: 0.8213 - loss: 0.4848 - val_accuracy: 0.9075 - val_loss: 0.3667
Epoch 8/250
1763/1763 ━━━━━━━━━━━━━━━━━━━━ 1s 344us/step - accuracy: 

## Part 4: Manual predictions from a trained neural net

In this part we will build predictions *manually* by extracting weights from the trained  `model2` and by constructing the transformations in the layers of the neural net ourselves.

### Task 4a)

Start this task by creating your own ReLU activation function. Save it as `ReLU`. Then, write your own sigmoid function for the output layer transformation. Save it as  `sigmoid`. 

In [39]:
# ReLU activation function
def ReLU(x):
    return np.maximum(0, x)

# Sigmoid activation function
def sigmoid(x):
    return 1 / (1 + np.exp(-x))

### Task 4b)
In the slides for lecture 8 we discussed how units in the different layers of a neural net look like. Now we are going to use the equations both hidden units and output unit to construct output predictions for the $n_{test}$ data points in `X_test`. Please do the following:

1. Apply the `get_weights()` method on `model2` to obtain a list object which stores the weights and biases of the learned model. Save it as `weight_and_bias_4b`.
2. Extract the objects inside `weight_and_bias_4b` into the objects for $\mathbf{b}_1,\mathbf{W}_1, \mathbf{b}_2, \mathbf{W}_2,\mathbf{b}_3, \mathbf{W}_3$ defined in the code chunk below.
3. Construct the linear term of the first layer hidden units and save these linear terms as a $30 \times n_{train}$ vector `Z_1`.
4. Construct the $15 \times n_{train}$ vector `Z_2` of linear terms for the second layer hidden units. Then, obtain the linear term of the output unit and save it as `Z_3`.
5. Put `Z_3` into the output layer activation function in order to get predictions for the probability of a Bud Light purchase. Save this as $n_{train} \times 1$ vector `pred_own_2b`. 

*Hint*: You can use `dim()` to check the dimension of matrices and `length()` to check that of vectors. Additionally, to ensure that you got the correct result for `prob_model2_own_4b` you can compare it with the output of `predict()`.

In [40]:
# 1. 
weight_and_bias_4b = model2.get_weights()

# 2. 
WW_1, bb_1, WW_2, bb_2, WW_3, bb_3 = weight_and_bias_4b

# 3. 
Z_1 = np.dot(X_test, WW_1) + bb_1  # Linear combination for the first layer

# 4.
Z_2 = np.dot(ReLU(Z_1),WW_2) + bb_2
Z_3 = np.dot(ReLU(Z_2),WW_3) + bb_3

# Apply sigmoid activation to Z_3
prob_model2_own_4b = sigmoid(Z_3)

In [41]:
print(prob_model2_own_4b)

[[0.46981479]
 [0.50482891]
 [0.3180558 ]
 ...
 [0.3995404 ]
 [0.54447135]
 [0.73448261]]


In [42]:
# Manually computed predictions using weights and biases
prob_model2_own_4b = sigmoid(Z_3)

# Compare with the predictions obtained from model2's predict method
pred_from_model = model2.predict(X_test)

print(pred_from_model)

# Ensure both predictions are close (numerically equivalent within a tolerance)
if np.allclose(prob_model2_own_4b, pred_from_model):
    print("The manually computed predictions match the predictions from model2!")
else:
    print("There is a mismatch between the manual predictions and the predict() method.")


572/572 ━━━━━━━━━━━━━━━━━━━━ 0s 258us/step
[[0.46981478]
 [0.5048289 ]
 [0.31805584]
 ...
 [0.39954036]
 [0.5444714 ]
 [0.7344826 ]]
The manually computed predictions match the predictions from model2!


In [44]:
print(f"Comparing the two arrays to check if their values are close enough within the default tolerance (rtol=1e-5, atol=1e-8). This way we can 'catch' small differences due to floating-point precision.")


Comparing the two arrays to check if their values are close enough within the default tolerance (rtol=1e-5, atol=1e-8). This way we can 'catch' small differences due to floating-point precision.
